# Who Goes There Prepare Flickr API

In [6]:
%reload_ext autoreload
%autoreload 2

import os
from os.path import join
from glob import glob, iglob
from pathlib import Path
from tqdm import tqdm_notebook as tqdm

import h5py
from scipy import misc
from io import BytesIO
from base64 import b64decode

from PIL import Image, ImageDraw
%matplotlib inline
import matplotlib.pyplot as plt
import scipy.io as sio
import h5py
import numpy as np
import pandas as pd

##  Create filepaths CSV for individual lookup

In [56]:
fp_flickr_meta = '/data_store/datasets/people/who_goes_there/research/wgt_flickr_queries.csv'
fp_filepaths = '/data_store/datasets/people/who_goes_there/research/who_goes_there_filepaths.csv'

In [57]:
df_flickr_meta = pd.read_csv(fp_flickr_meta)

In [58]:
help(pd.DataFrame.drop)

Help on function drop in module pandas.core.frame:

drop(self, labels=None, axis=0, index=None, columns=None, level=None, inplace=False, errors='raise')
    Drop specified labels from rows or columns.
    
    Remove rows or columns by specifying label names and corresponding
    axis, or by specifying directly index or column names. When using a
    multi-index, labels on different levels can be removed by specifying
    the level.
    
    Parameters
    ----------
    labels : single label or list-like
        Index or column labels to drop.
    axis : {0 or 'index', 1 or 'columns'}, default 0
        Whether to drop labels from the index (0 or 'index') or
        columns (1 or 'columns').
    index, columns : single label or list-like
        Alternative to specifying axis (``labels, axis=1``
        is equivalent to ``columns=labels``).
    
        .. versionadded:: 0.21.0
    level : int or level name, optional
        For MultiIndex, level from which the labels will be removed.

Index(['nickname', 'nsid', 'photo_id', 'url'], dtype='object')

In [64]:
df_flickr_meta.drop(labels=['subdir'],axis=1, inplace=True)
print(df_flickr_meta.keys())

Index(['nsid', 'photo_id', 'url'], dtype='object')


In [65]:
#df_flickr_meta['subdir'] = ''
df_flickr_meta['filepath'] = ''

In [67]:
pd.DataFrame.from_dict(df_flickr_meta).to_csv(fp_filepaths, index=False)

In [66]:
df_flickr_meta.head()

nsid    photo_id  \
0  51576145@N02  4762068863   
1  29689383@N02  5711730606   
2  29689383@N02  5711730606   
3  27982139@N00  2439203939   
4  27982139@N00  2464402099   

                                                 url filepath  
0  http://farm5.staticflickr.com/4117/4762068863_...           
1  http://farm3.staticflickr.com/2800/5711730606_...           
2  http://farm3.staticflickr.com/2800/5711730606_...           
3  http://farm3.staticflickr.com/2105/2439203939_...           
4  http://farm4.staticflickr.com/3030/2464402099_...

In [31]:
fp_in = '/data_store/datasets/people/who_goes_there/downloads/whogoesthere_dataset.hdf5'
fp_out = '/data_store/datasets/people/who_goes_there/research/wgt_flickr_meta_base.csv'

In [25]:
keys_all = ['accuracy', 'admin1', 'admin2', 'age', 'capture_device', 'city', 
  'content_length', 'country_code', 'date_taken', 'date_uploaded', 
  'description', 'face', 'face_bounds', 'face_key', 'face_landmarks_f', 
  'face_landmarks_o', 'gender', 'im_download_url', 'im_extension_original', 
  'im_farm_id', 'im_id', 'im_page_url', 'im_secret', 'im_secret_original', 
  'im_server_id', 'index', 'latitude', 'license_name', 'license_url', 'longitude', 
  'machine_tags', 'title', 'user_nickname', 'user_nsid', 'user_tags']

keys_keep = ['accuracy', 'admin1', 'admin2', 'age', 'capture_device', 'city', 
  'content_length', 'country_code', 'date_taken', 'date_uploaded', 
  'description', 'face', 'face_bounds', 'face_key', 'face_landmarks_f', 
  'face_landmarks_o', 'gender', 'im_download_url', 'im_extension_original', 
  'im_farm_id', 'im_id', 'im_page_url', 'im_secret', 'im_secret_original', 
  'im_server_id', 'index', 'latitude', 'license_name', 'license_url', 'longitude', 
  'machine_tags', 'title', 'user_nickname', 'user_nsid', 'user_tags']

In [44]:
results = []
with h5py.File(fp_in, 'r') as fp:
    print(fp.keys())
    print('')
    nsids = fp.get('user_nsid')
    for i, nsid in tqdm(enumerate(nsids), total=len(nsids)):
      obj = {
        'nsid': nsid.decode(),
        'photo_id': fp.get("im_id")[i],
        'url': fp.get("im_download_url")[i].decode(),
        'nickname': fp.get("user_nickname")[0].decode()
      }
      results.append(obj)

<KeysViewHDF5 ['accuracy', 'admin1', 'admin2', 'age', 'capture_device', 'city', 'content_length', 'country_code', 'date_taken', 'date_uploaded', 'description', 'face', 'face_bounds', 'face_key', 'face_landmarks_f', 'face_landmarks_o', 'gender', 'im_download_url', 'im_extension_original', 'im_farm_id', 'im_id', 'im_page_url', 'im_secret', 'im_secret_original', 'im_server_id', 'index', 'latitude', 'license_name', 'license_url', 'longitude', 'machine_tags', 'title', 'user_nickname', 'user_nsid', 'user_tags']>



In [45]:
df = pd.DataFrame.from_dict(results)
df.to_csv(fp_out, index=False)

In [46]:
df_flickr_meta_ext = '/data_store/datasets/people/who_goes_there/research/wgt_flickr_queries.csv'

## Convert Flickr Queries data to final meta file

In [54]:
fp_flickr_meta = '/data_store/datasets/people/who_goes_there/research/wgt_flickr_queries.csv'
fp_meta_out = '/data_store/datasets/people/who_goes_there/research/who_goes_there_flickr_meta.csv'

In [49]:
df_flickr_meta = pd.read_csv(fp_flickr_meta)

In [51]:
groups = df_flickr_meta.groupby('nsid')

In [53]:
results = []
for nsid, group in groups:
  obj = {
    'nsid': nsid,
    'count': len(group)
  }
  results.append(obj)

In [55]:
pd.DataFrame.from_dict(results).to_csv(fp_meta_out, index=False)